In [1]:
import cv2
import mediapipe as mp
import numpy as np
import pandas as pd

from os import walk
from google.cloud import storage


In [15]:
filenames = next(walk('/home/clement/code/ssaulay/silentspeak/drafts/data/sample_data/videos'), (None, None, []))[2] ### CHANGE FOR PRODUCTION


In [16]:
filenames = next(walk('/home/clement/code/ssaulay/silentspeak/drafts/data/sample_data/videos'), (None, None, []))[2] ### CHANGE FOR PRODUCTION
path_csv_normalize = "/home/clement/code/ssaulay/silentspeak/drafts/data/sample_data/csv/normalize/" ### CHANGE FOR PRODUCTION
path_csv_non_normalize = "/home/clement/code/ssaulay/silentspeak/drafts/data/sample_data/csv/non_normalize/" ### CHANGE FOR PRODUCTION

name_csv = []
for filename in filenames:
            
    path = f"/home/clement/code/ssaulay/silentspeak/drafts/data/sample_data/videos/{filename}"  ### CHANGE FOR PRODUCTION
    cap = cv2.VideoCapture(path)
    NUM_FACE = 2
    mp_face_mesh = mp.solutions.face_mesh
    mp_drawing = mp.solutions.drawing_utils
    faceMesh = mp_face_mesh.FaceMesh(max_num_faces=NUM_FACE)
    drawSpec = mp_drawing.DrawingSpec(thickness=1, circle_radius=1)

    coordinates_by_frames = []
    with mp_face_mesh.FaceMesh() as face_mesh:
        while cap.isOpened():
            ret, frame = cap.read()
            if not ret:
                break
            
            
            # Convert the BGR frame to RGB and process it
            rgb_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)

            # Process the frame using MediaPiSpe
            results = face_mesh.process(rgb_frame)  

            # Draw the face landmarks on the frame
            annotated_frame = frame.copy()
            
            if results.multi_face_landmarks:
                for faceLms in results.multi_face_landmarks:
                    mp_drawing.draw_landmarks(
                        annotated_frame,
                        results.multi_face_landmarks[0], 
                        mp_face_mesh.FACEMESH_CONTOURS,
                        drawSpec, 
                        drawSpec
                        )
            
            # Extract the mouth region
            mouth_coordinates = {}
            mouth_landmarks = []
            mouth_ids = [
            0, 267, 269, 270, 409, 291, 375, 321, 405, 314,
            17, 84, 181, 91, 146, 61, 185, 40, 39, 37, 0,
            13, 312, 311, 310, 415, 308, 324, 318, 402, 317,
            14, 87, 178, 88, 95, 78, 191, 80, 81, 82, 13
            ]
            reference_id = 6
            
            if results.multi_face_landmarks:
                landmarks = results.multi_face_landmarks[0]
                
                for id, landmark in enumerate(landmarks.landmark):
                    
                    # Extract only the mouth landmarks (IDs in mouth_ids)
                    if id in mouth_ids:
                        # Get the frame, id and coordinates of points of mouth
                        pos_frame = cap.get(cv2.CAP_PROP_POS_FRAMES)
                        coordinates_by_frames.append(pos_frame)
                        coordinates_by_frames.append(id)
                        coordinates_by_frames.append(landmark.x)
                        coordinates_by_frames.append(landmark.y)
                        coordinates_by_frames.append(landmark.z)
                        ih, iw, ip = frame.shape
                        x, y, z= int(landmark.x * iw), int(landmark.y * ih), int(landmark.y * ip)
                        mouth_landmarks.append((x, y))
                        mouth_coordinates[id] = landmarks
                        cv2.putText(frame, str(id), (x, y), cv2.FONT_HERSHEY_SIMPLEX, 0.8, (0, 255, 0), 1)
                        
                    if id == reference_id:
                        # Get the frame, id and coordinates of reference point
                        pos_frame = cap.get(cv2.CAP_PROP_POS_FRAMES)
                        coordinates_by_frames.append(pos_frame)
                        coordinates_by_frames.append(id)
                        coordinates_by_frames.append(landmark.x)
                        coordinates_by_frames.append(landmark.y)
                        coordinates_by_frames.append(landmark.z)
                        

            # Draw the mouth region
            if mouth_landmarks:
                hull = cv2.convexHull(np.array(mouth_landmarks))
                cv2.drawContours(annotated_frame, [hull], -1, (0, 255, 0), 2)

            # Show the video
            # cv2.imshow('Mouth Capture', annotated_frame)


            # Press 'q' to exit
            if cv2.waitKey(1) & 0xFF == ord('q'):
                break
            
        
    # Create dataframe from array
    coordinates_by_frames_array = [np.array(coordinates_by_frames[i:i+5]) for i in range(0, len(coordinates_by_frames), 5)]
    df = pd.DataFrame(coordinates_by_frames_array)
    df.rename(columns={0:'frame', 1:'point', 2:'x', 3:'y', 4:'z'}, inplace=True)
    
    # Add sentence and speaker
    df['sentence'] = filename[:-8]
    df['speaker'] = filename[4:-4]
    
    # Create csv non-scale
    name_csv = path_csv_non_normalize+filename[:-4]+".csv"
    df.to_csv(name_csv, index=False)
    
    # Dataframe scaled
    df_scale = df
    for i in range(0, df_scale['frame'].nunique()):
        # Get reference coordinates for ID 6 (at each frame)
        ref_x = df_scale.loc[df_scale['point'] == 6, 'x'].values[i]
        ref_y = df_scale.loc[df_scale['point'] == 6, 'y'].values[i]
        ref_z = df_scale.loc[df_scale['point'] == 6, 'z'].values[i]

        # Compute difference between coordinates (at each frame)
        df_scale['x'][df_scale['frame']==i+1] = df_scale['x'][df_scale['frame']==i+1] - ref_x
        df_scale['y'][df_scale['frame']==i+1] = df_scale['y'][df_scale['frame']==i+1] - ref_y
        df_scale['z'][df_scale['frame']==i+1] = df_scale['z'][df_scale['frame']==i+1] - ref_z
        
        # Create csv normalize
        name_csv_normalize = path_csv_normalize+filename[:-4]+"_normalize"+".csv"
        df_scale.to_csv(name_csv_normalize, index=False)


    cap.release()
    cv2.destroyAllWindows()

/tmp/ipykernel_6554/20889081.py:120: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_scale['x'][df_scale['frame']==i+1] = df_scale['x'][df_scale['frame']==i+1] - ref_x
/tmp/ipykernel_6554/20889081.py:121: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_scale['y'][df_scale['frame']==i+1] = df_scale['y'][df_scale['frame']==i+1] - ref_y
/tmp/ipykernel_6554/20889081.py:122: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_scale['z'][df_s

In [11]:
df

frame  point         x         y         z sentence speaker
0       1.0    0.0  0.001006  0.111432 -0.003280      001     L10
1       1.0    6.0  0.000000  0.000000  0.000000      001     L10
2       1.0   13.0  0.002309  0.123674  0.004015      001     L10
3       1.0   14.0  0.002622  0.159096  0.014245      001     L10
4       1.0   17.0  0.003141  0.180053  0.014900      001     L10
...     ...    ...       ...       ...       ...      ...     ...
2250   55.0  375.0  0.039870  0.142603  0.020534      001     L10
2251   55.0  402.0  0.021048  0.148008  0.013992      001     L10
2252   55.0  405.0  0.027410  0.163396  0.013019      001     L10
2253   55.0  409.0  0.039563  0.126263  0.016176      001     L10
2254   55.0  415.0  0.031000  0.127525  0.017226      001     L10

[2255 rows x 7 columns]